In [2]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
from sqlalchemy import create_engine
from sklearn import preprocessing
import mysql.connector
from pandas import DataFrame

# Load data

In [3]:
cases_repodb = pd.read_csv("./Data/Input/DISNET/final_cases_repodb.tsv", sep='\t')

In [4]:
cases_repodb = cases_repodb.drop(["Unnamed: 0"],axis=1)

In [6]:
triplets_repodb = pd.read_csv('./Data/Input/DISNET/repodb_all_triples.tsv', sep='\t')

In [9]:
triplets_repodb_one = triplets_repodb.rename(columns={"disease1": "disease_id","drug":"drug_id"})

In [10]:
triplets_repodb_one = triplets_repodb_one.drop_duplicates()

In [12]:
triplets_repodb_two = triplets_repodb.rename(columns={"disease2": "disease_id","drug":"drug_id"})

In [13]:
triplets_repodb_two = triplets_repodb_two.drop_duplicates()

In [15]:
join_one = cases_repodb.merge(triplets_repodb_one,how = "inner",on = ["drug_id","disease_id"])

In [17]:
join_two = cases_repodb.merge(triplets_repodb_two,how = "inner",on = ["drug_id","disease_id"])

In [18]:
join_two = join_two.drop_duplicates()

In [20]:
join_one_filter = join_one.drop(columns = ["disease_id","pathway_id","gene_id"])

In [22]:
join_two_filter = join_two.drop(columns = ["disease_id","pathway_id","gene_id"])

### 1. DRUG - GENE - TARGET

In [25]:
dis_gen = pd.read_csv('./Data/Input/DISNET/dis_genes.tsv', sep='\t')
dis_gen = dis_gen.drop(["Unnamed: 0"],axis=1)

In [27]:
dis_gen["score"].mean()

0.13747265487982685

In [28]:
gen_dise_join = joinone_csbj_diseases.merge(dis_gen,how = "inner",on = "disease_id")

In [30]:
drug_gen = pd.read_csv('./Data/Input/DISNET/drug_gen.tsv', sep='\t')
drug_gen = drug_gen.drop(["Unnamed: 0"],axis=1)

In [32]:
gen_dise_join_dru = gen_dise_join.merge(drug_gen,how = "inner",on = ["gene_id","drug_id"])

In [134]:
gen_dise_join_dru.to_csv("score_gdas_one_repodb.tsv", sep='\t')

In [34]:
gen_dise_join_dru["score"].mean()

0.1446285714285714

In [35]:
len(gen_dise_join_dru["disease_id"].unique())

24

###### JOIN TWO 

In [40]:
gen_dise_join_two = jointwo_csbj_diseases.merge(dis_gen,how = "inner",on = "disease_id")

In [41]:
gen_dise_join_dru_two = gen_dise_join_two.merge(drug_gen,how = "inner",on = ["gene_id","drug_id"])

In [133]:
gen_dise_join_dru_two.to_csv("score_gdas_two_repodb.tsv", sep='\t')

In [100]:
gen_dise_join_dru_two["score"].mean()

0.18121951219512178

In [43]:
len(gen_dise_join_dru_two["disease_id"].unique())

21

### 2.PATHWAYS

#### 2.1 Pathways direct 

In [44]:
dis_path_direct = pd.read_csv('./Data/Input/DISNET/disease_pathway.tsv', sep='\t')

In [49]:
joinone_csbj_diseases_fil = joinone_csbj_diseases.drop(["drug_id"],axis=1)

In [50]:
direct_dise_pw = joinone_csbj_diseases_fil.merge(dis_path_direct,how = "inner",on = "disease_id")

In [53]:
direct_dise_pw = direct_dise_pw.drop_duplicates()

In [54]:
len(direct_dise_pw["disease_id"].unique())

8

In [56]:
cases_repodb_filter = cases_repodb.drop(["drug_id","gene_id"],axis=1)

In [62]:
pws_direct_ori_new = direct_dise_pw.merge(cases_repodb_filter,how = "inner",on = ["disease_id","pathway_id"])

##### JOIN TWO

In [65]:
jointwo_csbj_diseases_fil = jointwo_csbj_diseases.drop(["drug_id"],axis=1)

In [66]:
direct_dise_pw_two = jointwo_csbj_diseases_fil.merge(dis_path_direct,how = "inner",on = "disease_id")

In [68]:
direct_dise_pw_two = direct_dise_pw_two.drop_duplicates()

In [69]:
len(direct_dise_pw_two["disease_id"].unique())

4

In [70]:
pws_direct_ori_new_two = direct_dise_pw_two.merge(cases_repodb_filter,how = "inner",on = ["disease_id","pathway_id"])

#### 2.2 Pathways via genes

In [73]:
dis_gen_pw = pd.read_csv('./Data/Input/DISNET/dis_gen_pw.tsv', sep='\t')
dis_gen_pw = dis_gen_pw.drop(["Unnamed: 0"],axis=1)

In [76]:
join_one_filter = join_one.drop(columns = ["disease_id","drug_id","gene_id"])

In [77]:
join_one_filter = join_one_filter.rename(columns={"disease2": "disease_id"})

In [78]:
pws_via_gen = join_one_filter.merge(dis_gen_pw,how = "inner",on = ["disease_id","pathway_id"])

In [80]:
len(pws_via_gen["disease_id"].unique())

29

In [91]:
pws_via_gen_final = pws_via_gen.merge(cases_repodb,how = "inner",on = ["disease_id","pathway_id","gene_id"])

In [82]:
join_two_filter = join_two.drop(columns = ["disease_id","drug_id","gene_id"])

In [83]:
join_two_filter = join_two_filter.rename(columns={"disease1": "disease_id"})

In [84]:
pws_via_gen_two = join_two_filter.merge(dis_gen_pw,how = "inner",on = ["disease_id","pathway_id"])

### 3. FINAL DATASET

In [122]:
join_one_re = join_one.rename(columns={"disease2": "disease_no_PwB"})

In [123]:
join_two_re = join_two.rename(columns={"disease1": "disease_no_PwB"})

In [124]:
all_triplets_repodb = pd.concat([join_one_re, join_two_re])

In [126]:
all_triplets_repodb = all_triplets_repodb.rename(columns={"disease_id": "disease_PwB"})

In [131]:
all_triplets_repodb.to_csv("all_triplets_repodb_union.tsv", sep='\t' )